In [1]:
'''
Created on Jun 24, 2018

@author: Mark Holton
'''

import sys
from _ast import Num
from array import array
import pandas as pd
import numpy as np
import copy

print("start")

start


In [2]:
#read the file in and
textfile = "./ag_map_with_alpha.txt"
originalDF=pd.read_csv(textfile,
                        sep = "\t")
masterDF=originalDF
#get a list of the column names
column_name_list=masterDF.columns.values.tolist()


C:\Users\Mark Holton\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2717: DtypeWarning: Columns (0,66) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
def Match( col_name, value_is_num, number_off=0):
    matchDF=masterDF
    matchDF['Matched to']='none'
    count_exper=0
    count_control=0
    while count_exper < matchDF.size:
        row = matchDF.loc[count_exper]
        if row.loc['control or experiment'] == 'exper':
            data_list=[]
            for col in col_name:
                col_value = row.loc(col)
                if(col_value == 'Unspecified'):
                    print("error some info not given for " + row.loc["#SampleID"])
                    count_exper = count_exper + 1
                    continue
                data_list.append(col_value)
                
            count_control=0
            while count_control < matchDF.size:
                row_match = matchDF.loc[count_control]
                if row_match.loc['control or experiment'] == 'control':
                    list_counter = 0
                    is_match = True
                    for col in col_name:
                        col_match_value = row_match.loc(col)
                        if(col_match_value == 'Unspecified'):
                            print("error some info not given for " + row_match.loc["#SampleID"])
                            count_control = count_control + 1
                            continue
                        if(value_is_num == 'False' 
                          and data_list.at(list_counter) != col_match_value ):
                            # match not found
                            is_match = False
                            count_control = count_control + 1
                            continue
                        if(value_is_num == 'True' 
                          and ( int(data_list.at(list_counter)) - number_off ) <= int(col_match_value)
                          and ( int(data_list.at(list_counter)) + number_off ) >= int(col_match_value) ):
                            # match not found
                            is_match = False
                            count_control = count_control + 1
                            continue
                        # if above cases not met then the row could still be a match
                        list_counter = list_counter + 1
                    
                    if is_match == True:
                        matchDF.loc[count_control, 'Matched to'] = row.loc['#SampleID']
                    count_control = count_control + 1
                
                count_exper = count_exper + 1

    return matchDF






In [4]:
user_input_exclude = 'exclude' # input("Filename for file with column and data to exclude: ")
user_input_exclude_in_match = False # input('Is the "exclude" data to be excluded or kept (T for excluded and F for kept') == 'T'
user_input_control = 'control' # input("Filename for file with column and data to determine control: ")
user_input_experiment = 'experiment' # input("Filename for file with column and data to determine experimental: ")
user_input_match = 'match' # input("Filename for file with columns, type of value, and offset if needed to match samples: ")


user_input_exclude = './' + user_input_exclude + '.txt'
user_input_control = './' + user_input_control + '.txt'
user_input_experiment = './' + user_input_experiment + '.txt'
user_input_match= './' + user_input_match + '.txt'


print(user_input_exclude)
print(user_input_exclude_in_match)
print(user_input_control)
print(user_input_experiment)
print(user_input_match)

./exclude.txt
False
./control.txt
./experiment.txt
./match.txt


In [5]:
user_input_excludeDF = pd.read_csv(user_input_exclude, sep = "\t")
user_input_controlDF = pd.read_csv(user_input_control, sep = "\t")
user_input_experimentDF = pd.read_csv(user_input_experiment, sep = "\t")
user_input_matchDF = pd.read_csv(user_input_match, sep = "\t")

#colum_input_list has eclude column first, then control, and then the match columns
#control and experimental column should be the same
column_input_list=user_input_excludeDF.columns.values.tolist() + ['con'] + user_input_controlDF.columns.values.tolist() +  ['match'] +user_input_matchDF.columns.values.tolist() 
column_input_list

['antibiotic_history',
 'con',
 'depression_bipolar_schizophrenia',
 'mental_illness_type_depression',
 'match',
 'bmi_cat',
 'age_years',
 'smoking_frequency']

In [6]:
def Drop_Rows(exclude_if_match,colum_name , list_values_to_determine_exclution):
    #if list values match a row in a column then the row is excluded
    count = 0
    retDF = masterDF
    for col in colum_name:
        print('col= ' + col)
        for element in masterDF[ col ]:
            if (count % 500 == 0):
               print(count)
            if exclude_if_match == True:
                #if list values match a row in a column then the row is excluded
                for value in list_values_to_determine_exclution:
                    if(element == value):
                        retDF = retDF.drop( count)
            if exclude_if_match == False:
                #if list values match a row in a column then the row is not excluded
                dont_drop = False
                for value in list_values_to_determine_exclution:
                    if element == value:
                        dont_drop = True
                if(dont_drop == False):
                    retDF = retDF.drop(count)
            count = count + 1

    return retDF

In [7]:
masterDF = copy.deepcopy(originalDF)
while_count = 0
while column_input_list[while_count] != 'con':
    col_name = column_input_list[while_count] 
    print(col_name )
    col_data = user_input_excludeDF[col_name].tolist()
    print(user_input_exclude_in_match)
    masterDF = Drop_Rows(user_input_exclude_in_match, [col_name] , col_data)
    while_count = while_count + 1
print("done")
masterDF = masterDF.reset_index(drop=True)
excludeDF = copy.deepcopy(masterDF)


antibiotic_history
False
col= antibiotic_history
0
500
1000
1500
2000
2500
3000
3500
4000
4500
5000
5500
6000
6500
7000
7500
done


In [12]:
def Lable_Controls_and_Exper(colum_name, list_values_to_determine_control, list_values_to_determine_exper):
    for col in colum_name:
        index = 0
        print(col+':')
        print(masterDF[col])
        for element in masterDF[col]:
            #print(index)
            #if list values match a row in a column then the row is excluded
            for value in list_values_to_determine_control:
                #print(masterDF.loc[index,'control or experiment'] + "here")
                    
                if(element == value 
                    and masterDF.loc[index,'control_or_experiment'] != 'exper'):
                    masterDF.loc[index,'control_or_experiment'] = 'control'
                        
            for value in list_values_to_determine_exper:
                if(element == value):
                    masterDF.loc[ index, 'control_or_experiment' ] = 'exper'
                        
            index = index + 1 
        masterDF

In [ ]:
masterDF = copy.deepcopy(excludeDF)
while_count_two = while_count + 1
print(while_count_two)
masterDF['control_or_experiment'] = 'none'
#masterDF.assign(control_or_experiment = 'none')

while column_input_list[while_count_two] != 'match':
    col_name = column_input_list[while_count_two] 
    col_data_control = user_input_controlDF[col_name].tolist()
    col_data_exper = user_input_experimentDF[col_name].tolist()   
    masterDF = Lable_Controls_and_Exper([col_name], col_data_control, col_data_exper)
    while_count_two = while_count_two + 1
print("done")
exper_controlDF = copy.deepcopy(masterDF)
masterDF


 
    


2
depression_bipolar_schizophrenia:
            #SampleID       barcode center_name center_project_name  \
0     10317.000049761  TCCGGACTCCTG      UCSDMI                AG30   
1     10317.000040165  CAGTCCCTGCAC      UCSDMI                AG28   
2     10317.000030322  AATAGATGCTGA      UCSDMI                AG22   
3     10317.000028857  CCAGTATCGCGT      UCSDMI                AG19   
4     10317.000038189  TATAATCCGAGG      UCSDMI     AGp.109.110.111   
5     10317.000001281  CCTACCATTGTT      UCSDMI                 AG2   
6     10317.000036487  CGGATCTAGTGT      UCSDMI                AG23   
7     10317.000030166  AGGACAAACTAT      UCSDMI                AG21   
8     10317.000023295  TATCCAAGCGCA      UCSDMI                AG18   
9     10317.000001589  GTTAGGGAGCGA      UCSDMI                 AG1   
10    10317.000030991  AGCTCTAGAAAC      UCSDMI                AG21   
11    10317.000003505  ACCCGGATTTCG      UCSDMI                 AG1   
12    10317.000021163  GGACCTGGATGG      

TypeError: 'NoneType' object is not subscriptable

In [30]:

    



print("done")
   

done


In [29]:
column_name_list

['#SampleID',
 'barcode',
 'center_name',
 'center_project_name',
 'comments_renamed',
 'condition_renamed',
 'experiment_center',
 'experiment_design_description',
 'experiment_title',
 'extraction_robot',
 'extractionkit_lot',
 'instrument_model',
 'library_construction_protocol',
 'linker',
 'mastermix_lot',
 'orig_name',
 'pcr_primers',
 'plateid',
 'platform',
 'plating',
 'primer',
 'primer_date',
 'primer_plate',
 'primerplate_renamed',
 'processing_robot',
 'project_name',
 'qiita_prep_id',
 'run_center',
 'run_date',
 'run_prefix',
 'samp_size',
 'sample_center',
 'sample_plate',
 'sequencing_meth',
 'target_gene',
 'target_subfragment',
 'tm1000_8_tool',
 'tm300_8_tool',
 'tm50_8_tool',
 'water_lot',
 'well',
 'well_description',
 'well_id',
 'acid_reflux',
 'acne_medication',
 'acne_medication_otc',
 'add_adhd',
 'age_cat',
 'age_corrected',
 'age_years',
 'alcohol_consumption',
 'alcohol_frequency',
 'alcohol_types_beercider',
 'alcohol_types_red_wine',
 'alcohol_types_sour

In [23]:
originalDF

#SampleID       barcode center_name center_project_name  \
0     10317.000028848  CAAACGCACTAA      UCSDMI                AG19   
1     10317.000049761  TCCGGACTCCTG      UCSDMI                AG30   
2     10317.000059054  ACACTCATTACT      UCSDMI           AG3dMouse   
3     10317.000040165  CAGTCCCTGCAC      UCSDMI                AG28   
4     10317.000030322  AATAGATGCTGA      UCSDMI                AG22   
5     10317.000028169  GCACGCGAGCAC      UCSDMI                AG20   
6     10317.000028857  CCAGTATCGCGT      UCSDMI                AG19   
7     10317.000001386  CGTCGTCTAAGA      UCSDMI                 AG1   
8     10317.000038189  TATAATCCGAGG      UCSDMI     AGp.109.110.111   
9     10317.000001281  CCTACCATTGTT      UCSDMI                 AG2   
10    10317.000036487  CGGATCTAGTGT      UCSDMI                AG23   
11    10317.000030166  AGGACAAACTAT      UCSDMI                AG21   
12    10317.000023295  TATCCAAGCGCA      UCSDMI                AG18   
13    10317.000001589  GTTAGGGAGCGA      UCSDMI                 AG1   
14    10317.000030991  AGCTCTAGAAAC      UCSDMI                AG21   
15    10317.000003505  ACCCGGATTTCG      UCSDMI                 AG1   
16    10317.000021163  GGACCTGGATGG      UCSDMI                AG17   
17    10317.000052269  GCACCAATCTGC      UCSDMI              AGag33   
18    10317.000059006  GTGCGAGGACAA      UCSDMI           AG3dMouse   
19    10317.000023087  ATTTGCTTTGCC      UCSDMI                AG17   
20    10317.000029448  TCATCCGTCGGC      UCSDMI                AG21   
21    10317.000031342  GTTGTTCTGGGA      UCSDMI                AG21   
22    10317.000029161  CCAGGACAGGAA      UCSDMI                AG21   
23    10317.000009132  CCTACCATTGTT      UCSDMI                AG10   
24    10317.000009158  CCTTCTGTATAC      UCSDMI                 AG5   
25    10317.000030426  AATATCGGGATC      UCSDMI              AGag36   
26    10317.000017750  GAAGCTTGAATC      UCSDMI                AG14   
27    10317.000020516  TAAGACTACTGG      UCSDMI                AG19   
28    10317.000012512  TGCAAGCTAAGT      UCSDMI         AGagOffice2   
29    10317.000011934  TTCACCTGTATC      UCSDMI                 AG7   
...               ...           ...         ...                 ...   
7682            10317  CTGAGGCCCTTC      UCSDMI                AG28   
7683            10317  AATCTTGCGCCG      UCSDMI                 AG1   
7684            10317  TGTGGAAACTCC      UCSDMI                AG14   
7685            10317  CATTCAGTTATA      UCSDMI              AGag34   
7686            10317  ACCAATCTCGGC      UCSDMI                 AG3   
7687            10317  CGTTTATCCGTT      UCSDMI              AGag36   
7688            10317  ATGTCACCGCTG      UCSDMI                 AG1   
7689            10317  GCGATGGCGATG      UCSDMI                AG27   
7690            10317  GCGAGGAAGTCC      UCSDMI              AGag33   
7691            10317  GGTGTGAGAAAG      UCSDMI                AG23   
7692            10317  ACTAAGTACCCG      UCSDMI                AG21   
7693            10317  CGTTCCTTGTTA      UCSDMI                AG20   
7694            10317  AGACAGTAGGAG      UCSDMI              AGag35   
7695            10317  GTCGTTACCCGC      UCSDMI                AG21   
7696            10317  CAGTTCGAGATA      UCSDMI                 AG1   
7697            10317  GTTAACTTACTA      UCSDMI              AGag35   
7698            10317  ACACCGCACAAT      UCSDMI                 AG1   
7699            10317  TTGCCTGGGTCA      UCSDMI                AG19   
7700            10317  ATATGACCCAGC      UCSDMI                 AG8   
7701            10317  TGCAACTTGCAG      UCSDMI     AGp.109.110.111   
7702            10317  ACGGGATACAGG      UCSDMI                 AG2   
7703            10317  TAAGAAACGTCA      UCSDMI            AGAGA.RR   
7704            10317  TAGTGTCGGATC      UCSDMI              AGag34   
7705            10317  TCAAGATCAAGA      UCSDMI                AG27   
7706            10317  CTCTTCTGATCA 